In [1]:
from pyspark.sql import SparkSession
from operator import add


# Spark session
spark_session = SparkSession\
        .builder\
        .master("spark://192.168.2.218:7077") \
        .appName("Scalingtest")\
        .config("spark.executor.cores",2)\
        .config("spark.dynamicAllocation.enabled", True)\
        .config("spark.dynamicAllocation.shuffleTracking.enabled", True)\
        .config("spark.shuffle.service.enabled", False)\
        .config("spark.dynamicAllocation.executorIdleTimeout","30s")\
        .config("spark.driver.port",9998)\
        .config("spark.blockManager.port",10005)\
        .config("spark.executor.memory","2g")\
        .getOrCreate()

# Spark context
spark_context = spark_session.sparkContext

spark_context.setLogLevel("INFO")

Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
22/03/10 10:09:39 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
22/03/10 10:09:41 WARN ExecutorAllocationManager: Dynamic allocation without a shuffle service is an experimental feature.


In [2]:
#loop to append file paths for each parent directory
root ='hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/'
letters = ['A','B','C','E','G','J','K','L','M','N','O','P','Q','R','S','T','U','W','X','Y','Z']
paths=[]
for i in letters:
    paths.append(root+i)
paths[-1]

'hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/Z'

In [ ]:
#starting timing and run all cells below to measure wall time
import time
start = time.time()

#read in files from parent directories choose how may by slicing the paths list in the loop
data = spark_session.read.option("recursiveFileLookup", "true").json(paths[0]).cache()
data.count()
for i in paths[1:6]:
    temp = spark_session.read.option("recursiveFileLookup", "true").json(i).cache()
    data = data.union(temp)


#data = spark_session.read.json('hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/B/A/A/*.json')

22/03/10 10:09:45 INFO InMemoryFileIndex: It took 1827 ms to list leaf files for 1 paths.
22/03/10 10:09:47 INFO HadoopFSUtils: Listing leaf files and directories in parallel under 10829 paths. The first several paths are: hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABAAA128F9309349.json, hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABAAX128F14914F9.json, hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABACN128F425B784.json, hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABADO128F14599E2.json, hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABAFE128F93235DB.json, hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABAFJ128F42AF24E.json, hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABAFP128F931E9A1.json, hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABAFS128F4235B31.json, hdfs://192.168.2.200:9000/user/ubuntu/lastfm_train/A/B/A/TRABAGD128F422302C.json, hdfs://192.168.2.200:9000/user/ubuntu/l

In [ ]:
# Flatten the tags column
from pyspark.sql.functions import flatten
dataframe = data.withColumn("New tags", flatten(data.tags))

In [ ]:
# Remove the numbers from the tags (the numbers are every other element)
from pyspark.sql.types import ArrayType, StringType
from pyspark.sql.functions import udf, col

removeNumbers = udf(lambda lst: lst[0::2], ArrayType(StringType()))

dataFrame = dataframe.withColumn("Only tags", removeNumbers(col("New tags")))

In [ ]:
import re
# Function for determine if a song has been tagged with a tag including "male" or "female" or both
def genderTags(lst):
    genderList = []
    for element in lst:
        if re.search("female|Female", element) and "female" not in genderList:
            genderList.append("female")
            continue
        elif re.search("male|Male", element) and "male" not in genderList:
            genderList.append("male")
            continue
        
    return genderList

# Create udf from the above function
genderTagUDF = udf(genderTags, ArrayType(StringType()))

# Create a new column representing wether a song has been tagged with "female", "male" or both
dataframe = dataFrame.withColumn("Gender tag", genderTagUDF(col("Only tags")))
        

In [ ]:
# Function for removing the gender tag from the tags
def removeGenderTags(lst):
    tags = []
    for element in lst:
        if re.search("female|Female", element) or re.search("male|Male", element):
            continue
        else:
            tags.append(element)
        
        
    return tags

# Create udf from the above function
removeGenderTagUDF = udf(removeGenderTags, ArrayType(StringType()))

# Create a new column where the"female" and "male" tags have been removed from the other tags
filteredDF = dataframe.withColumn("Tags", removeGenderTagUDF(col("Only tags")))

In [ ]:
# Create new dataframe with only the tags and the gender tag
genderDataFrame = filteredDF.select("Tags", "Gender tag")

In [ ]:
# Explode the tags column
from pyspark.sql.functions import explode
genderDataFrame = genderDataFrame.select(genderDataFrame["Gender tag"], explode(genderDataFrame["Tags"]))
genderDataFrame = genderDataFrame.withColumnRenamed("col", "Tag")

In [ ]:
# Explode the gender tag column
genderDataFrame = genderDataFrame.select(explode(genderDataFrame["Gender tag"]), genderDataFrame["Tag"])
genderDataFrame = genderDataFrame.withColumnRenamed("col", "Gender")


In [ ]:
# Find the most frequent tags for "female"
tagsFemale = genderDataFrame.select("Tag").filter(genderDataFrame["Gender"] == "female").groupBy("Tag").agg({"Tag": "count"})\
        .withColumnRenamed("count(Tag)","Frequency").orderBy("Frequency", ascending=False)

tagsFemale.show()

In [ ]:
# Find the most frequent tags for "male"
tagsMale = genderDataFrame.select("Tag").filter(genderDataFrame["Gender"] == "male").groupBy("Tag").agg({"Tag": "count"})\
        .withColumnRenamed("count(Tag)","Frequency").orderBy("Frequency", ascending=False)

print(tagsMale.show())
print()
print(f'execution time in minutes: {(time.time()-start)/60}')



In [ ]:
data.count()


In [ ]:
# spark_session.stop()